# 🧠 LangGraph Übungen für Finance, Risk und Controlling

In diesem Notebook werden wir schrittweise einen LangGraph für Anwendungsfälle im Finanz- und Risikobereich aufbauen. Die Übungen sind speziell für Fachkräfte aus Finance, Risk und Controlling konzipiert und erfordern keine umfangreiche Programmiererfahrung.

## 📚 Voraussetzungen installieren

Zuerst müssen wir die notwendigen Bibliotheken installieren:

In [ ]:
!pip install langchain langgraph langchain-openai

## 🔑 API-Schlüssel einrichten

Für die Verwendung von OpenAI-Modellen benötigen wir einen API-Schlüssel:

In [ ]:
import os
import yaml

# Option 1: Direkt im Code (nicht für Produktionsumgebungen empfohlen)
# os.environ["OPENAI_API_KEY"] = "Ihr-API-Schlüssel"

# Option 2: Aus einer YAML-Datei laden (sicherer)
try:
    OPENAI_API_KEY = yaml.safe_load(open("../credentials.yml"))["openai"]
    os.environ["OPENAI_API_KEY"] = OPENAI_API_KEY
    print("API-Schlüssel erfolgreich geladen!")
except:
    print("Bitte geben Sie Ihren OpenAI API-Schlüssel ein:")
    os.environ["OPENAI_API_KEY"] = input()

## 🧩 Übung 1: Einfacher LangGraph für Risikoklassifizierung

In dieser ersten Übung erstellen wir einen einfachen LangGraph, der Finanzrisiken klassifiziert und entsprechend weiterleitet.

In [ ]:
from typing import TypedDict, Optional, Literal, List, Dict, Any
from langchain_openai import ChatOpenAI
from langchain_core.prompts import ChatPromptTemplate
from langgraph.graph import StateGraph, END

# LLM initialisieren
llm = ChatOpenAI(model="gpt-3.5-turbo", temperature=0)

### Schritt 1: Zustandstyp definieren

Zuerst definieren wir, welche Daten in unserem Graphen fließen sollen:

In [ ]:
class RiskState(TypedDict):
    """Zustand für unseren Risiko-Klassifizierungs-Graphen"""
    # Eingabe: Beschreibung des zu bewertenden Risikos
    risk_description: str
    # Ausgabe: Klassifizierung des Risikos (hoch, mittel, niedrig)
    risk_level: Optional[str]
    # Ausgabe: Detaillierte Analyse
    analysis: Optional[str]
    # Ausgabe: Empfohlene Maßnahmen
    recommended_actions: Optional[str]

### Schritt 2: Knoten-Funktionen definieren

Jetzt definieren wir die Funktionen, die als Knoten in unserem Graphen dienen werden:

In [ ]:
def classify_risk(state: RiskState) -> Dict[str, Any]:
    """Klassifiziert das Risiko als hoch, mittel oder niedrig."""
    # Prompt für die Risikoklassifizierung
    prompt = ChatPromptTemplate.from_template("""
    Du bist ein Experte für Risikomanagement im Finanzbereich.
    
    Bitte klassifiziere das folgende Risiko als "hoch", "mittel" oder "niedrig":
    
    {risk_description}
    
    Antworte nur mit einem Wort: "hoch", "mittel" oder "niedrig".
    """)
    
    # LLM aufrufen
    risk_level = llm.invoke(prompt.format(risk_description=state["risk_description"]))
    
    # Rückgabe: Nur das risk_level wird aktualisiert
    return {"risk_level": risk_level.content.strip().lower()}

In [ ]:
def analyze_high_risk(state: RiskState) -> Dict[str, Any]:
    """Detaillierte Analyse für Hochrisiko-Fälle."""
    prompt = ChatPromptTemplate.from_template("""
    Du bist ein Senior Risk Manager im Finanzbereich.
    
    Analysiere das folgende HOCHRISIKO-Szenario detailliert:
    
    {risk_description}
    
    Liefere eine strukturierte Analyse mit folgenden Punkten:
    1. Hauptrisikofaktoren
    2. Potenzielle finanzielle Auswirkungen
    3. Regulatorische Bedenken
    4. Empfohlene sofortige Maßnahmen
    """)
    
    analysis = llm.invoke(prompt.format(risk_description=state["risk_description"]))
    
    return {"analysis": analysis.content}

def analyze_medium_risk(state: RiskState) -> Dict[str, Any]:
    """Detaillierte Analyse für mittlere Risiken."""
    prompt = ChatPromptTemplate.from_template("""
    Du bist ein Risk Analyst im Finanzbereich.
    
    Analysiere das folgende MITTLERE Risiko:
    
    {risk_description}
    
    Liefere eine strukturierte Analyse mit folgenden Punkten:
    1. Risikofaktoren
    2. Mögliche Auswirkungen
    3. Empfohlene Überwachungsmaßnahmen
    """)
    
    analysis = llm.invoke(prompt.format(risk_description=state["risk_description"]))
    
    return {"analysis": analysis.content}

def analyze_low_risk(state: RiskState) -> Dict[str, Any]:
    """Einfache Analyse für Niedrigrisiko-Fälle."""
    prompt = ChatPromptTemplate.from_template("""
    Du bist ein Junior Risk Analyst im Finanzbereich.
    
    Fasse das folgende NIEDRIGE Risiko kurz zusammen:
    
    {risk_description}
    
    Liefere eine kurze Zusammenfassung und Standardmaßnahmen.
    """)
    
    analysis = llm.invoke(prompt.format(risk_description=state["risk_description"]))
    
    return {"analysis": analysis.content}

In [ ]:
def recommend_actions(state: RiskState) -> Dict[str, Any]:
    """Empfiehlt konkrete Maßnahmen basierend auf der Analyse."""
    prompt = ChatPromptTemplate.from_template("""
    Du bist ein Risikomanagement-Experte im Finanzbereich.
    
    Basierend auf der folgenden Risikoanalyse, empfehle konkrete Maßnahmen:
    
    Risikobeschreibung: {risk_description}
    Risikolevel: {risk_level}
    Analyse: {analysis}
    
    Formuliere 3-5 konkrete, umsetzbare Maßnahmen als nummerierte Liste.
    """)
    
    actions = llm.invoke(
        prompt.format(
            risk_description=state["risk_description"],
            risk_level=state["risk_level"],
            analysis=state["analysis"]
        )
    )
    
    return {"recommended_actions": actions.content}

### Schritt 3: Routing-Funktion definieren

Diese Funktion entscheidet, welcher Analyse-Knoten basierend auf dem Risikolevel verwendet werden soll:

In [ ]:
def route_by_risk_level(state: RiskState) -> str:
    """Routing-Funktion basierend auf dem Risikolevel."""
    risk_level = state["risk_level"]
    
    if "hoch" in risk_level:
        return "analyze_high_risk"
    elif "mittel" in risk_level:
        return "analyze_medium_risk"
    else:
        return "analyze_low_risk"

### Schritt 4: Graph erstellen und kompilieren

In [ ]:
# Graph erstellen
workflow = StateGraph(RiskState)

# Knoten hinzufügen
workflow.add_node("classify_risk", classify_risk)
workflow.add_node("analyze_high_risk", analyze_high_risk)
workflow.add_node("analyze_medium_risk", analyze_medium_risk)
workflow.add_node("analyze_low_risk", analyze_low_risk)
workflow.add_node("recommend_actions", recommend_actions)

# Kanten definieren
workflow.add_edge("classify_risk", route_by_risk_level)
workflow.add_edge("analyze_high_risk", "recommend_actions")
workflow.add_edge("analyze_medium_risk", "recommend_actions")
workflow.add_edge("analyze_low_risk", "recommend_actions")
workflow.add_edge("recommend_actions", END)

# Startknoten festlegen
workflow.set_entry_point("classify_risk")

# Graph kompilieren
risk_app = workflow.compile()

### Schritt 5: Graph visualisieren (optional)

Wenn Sie die Struktur Ihres Graphen visualisieren möchten:

In [ ]:
try:
    from langgraph.graph import visualize
    visualize(workflow)
except ImportError:
    print("Visualisierung nicht verfügbar. Installieren Sie graphviz für die Visualisierung.")

### Schritt 6: Graph testen

Jetzt können wir unseren Graphen mit verschiedenen Risikoszenarien testen:

In [ ]:
# Beispiel 1: Hohes Risiko
high_risk_example = {
    "risk_description": "Ein großer Kunde (20% des Umsatzes) hat Insolvenz angemeldet und ausstehende Forderungen von 2 Millionen Euro können möglicherweise nicht beglichen werden."
}

# Graph ausführen
result = risk_app.invoke(high_risk_example)

# Ergebnisse anzeigen
print(f"Risikolevel: {result['risk_level']}\n")
print(f"Analyse:\n{result['analysis']}\n")
print(f"Empfohlene Maßnahmen:\n{result['recommended_actions']}")

In [ ]:
# Beispiel 2: Mittleres Risiko
medium_risk_example = {
    "risk_description": "Die Währungsschwankungen zwischen Euro und Dollar haben in den letzten drei Monaten zu Verlusten von 5% bei internationalen Transaktionen geführt."
}

# Graph ausführen
result = risk_app.invoke(medium_risk_example)

# Ergebnisse anzeigen
print(f"Risikolevel: {result['risk_level']}\n")
print(f"Analyse:\n{result['analysis']}\n")
print(f"Empfohlene Maßnahmen:\n{result['recommended_actions']}")

In [ ]:
# Beispiel 3: Niedriges Risiko
low_risk_example = {
    "risk_description": "Ein neues Buchhaltungssystem wird eingeführt, was kurzfristig zu erhöhtem Schulungsbedarf führt, aber keine direkten finanziellen Auswirkungen hat."
}

# Graph ausführen
result = risk_app.invoke(low_risk_example)

# Ergebnisse anzeigen
print(f"Risikolevel: {result['risk_level']}\n")
print(f"Analyse:\n{result['analysis']}\n")
print(f"Empfohlene Maßnahmen:\n{result['recommended_actions']}")

## 🧩 Übung 2: Dokumentenklassifikation und Routing

In dieser Übung erstellen wir einen LangGraph, der Finanzdokumente klassifiziert und an die entsprechenden Expertenknoten weiterleitet.

### Schritt 1: Zustandstyp definieren

In [ ]:
class DocumentState(TypedDict):
    """Zustand für unseren Dokumentenklassifizierungs-Graphen"""
    # Eingabe: Dokumenteninhalt oder -beschreibung
    document_content: str
    # Ausgabe: Dokumententyp (Bilanz, ESG-Bericht, Vertrag, etc.)
    document_type: Optional[str]
    # Ausgabe: Extrahierte Schlüsselinformationen
    key_information: Optional[str]
    # Ausgabe: Zusammenfassung oder Analyse
    analysis: Optional[str]

### Schritt 2: Knoten-Funktionen definieren

In [ ]:
def classify_document(state: DocumentState) -> Dict[str, Any]:
    """Klassifiziert den Dokumenttyp."""
    prompt = ChatPromptTemplate.from_template("""
    Du bist ein Experte für Finanzdokumente.
    
    Klassifiziere das folgende Dokument in eine der folgenden Kategorien:
    - Bilanz
    - ESG-Bericht
    - Vertrag
    - Risikobericht
    - Sonstiges
    
    Dokumentinhalt:
    {document_content}
    
    Antworte nur mit einem Wort aus der obigen Liste.
    """)
    
    document_type = llm.invoke(prompt.format(document_content=state["document_content"]))
    
    return {"document_type": document_type.content.strip()}

In [ ]:
# Weitere Knoten-Funktionen für verschiedene Dokumenttypen
# Diese können Sie als Übung selbst implementieren!

def analyze_balance_sheet(state: DocumentState) -> Dict[str, Any]:
    """Analysiert eine Bilanz."""
    # Implementieren Sie diese Funktion als Übung
    prompt = ChatPromptTemplate.from_template("""
    Du bist ein Finanzanalyst, spezialisiert auf Bilanzen.
    
    Analysiere die folgende Bilanz und extrahiere die wichtigsten Kennzahlen:
    {document_content}
    
    Liefere eine strukturierte Analyse mit:
    1. Wichtigste Finanzkennzahlen
    2. Vermögenswerte und Verbindlichkeiten
    3. Auffälligkeiten und Trends
    """)
    
    analysis = llm.invoke(prompt.format(document_content=state["document_content"]))
    
    return {"analysis": analysis.content}

def analyze_esg_report(state: DocumentState) -> Dict[str, Any]:
    """Analysiert einen ESG-Bericht."""
    # Implementieren Sie diese Funktion als Übung
    prompt = ChatPromptTemplate.from_template("""
    Du bist ein ESG-Spezialist.
    
    Analysiere den folgenden ESG-Bericht und extrahiere die wichtigsten Informationen:
    {document_content}
    
    Liefere eine strukturierte Analyse mit:
    1. Umweltkennzahlen und -ziele
    2. Soziale Verantwortung und Maßnahmen
    3. Governance-Strukturen
    4. Stärken und Verbesserungspotenziale
    """)
    
    analysis = llm.invoke(prompt.format(document_content=state["document_content"]))
    
    return {"analysis": analysis.content}

# Weitere Analysefunktionen können Sie als Übung implementieren

### Schritt 3: Routing-Funktion definieren

In [ ]:
def route_by_document_type(state: DocumentState) -> str:
    """Routing-Funktion basierend auf dem Dokumenttyp."""
    doc_type = state["document_type"].lower()
    
    if "bilanz" in doc_type:
        return "analyze_balance_sheet"
    elif "esg" in doc_type:
        return "analyze_esg_report"
    # Weitere Routing-Optionen können Sie als Übung implementieren
    else:
        return "generic_analysis"

### Schritt 4: Graph erstellen (als Übung)

Implementieren Sie den Dokumentenklassifizierungs-Graph als Übung, basierend auf dem vorherigen Beispiel.

In [ ]:
# Ihre Implementierung hier
# ...

# Beispiel für die Struktur:
'''
doc_workflow = StateGraph(DocumentState)
doc_workflow.add_node("classify_document", classify_document)
doc_workflow.add_node("analyze_balance_sheet", analyze_balance_sheet)
doc_workflow.add_node("analyze_esg_report", analyze_esg_report)
# ...

doc_workflow.add_edge("classify_document", route_by_document_type)
# ...

doc_app = doc_workflow.compile()
'''

## 🧪 Herausforderung: Erweiterte Routing-Logik

Als fortgeschrittene Übung können Sie versuchen, einen komplexeren Graphen zu erstellen, der mehrere Entscheidungspunkte und Feedback-Schleifen enthält. Zum Beispiel:

1. Dokument klassifizieren
2. Relevante Informationen extrahieren
3. Risikobewertung durchführen
4. Bei hohem Risiko: Zusätzliche Prüfung anfordern
5. Bei niedrigem Risiko: Automatisch genehmigen

Diese Übung überlassen wir Ihnen als Herausforderung!